# Testing data access from esgf
Some model can be loaded from xarray without pb, some have pb.  this notebook, we load 'CMCC-CM2-HR4'

This example worked like 5 minutes ago, and now does not work anymore.


## Import packages

In [1]:
%matplotlib inline
import xarray as xr
import s3fs
import zarr


In [2]:
"""This is a general purpose module containing routines
(a) that are used in multiple notebooks; or 
(b) that are complicated and would thus otherwise clutter notebook design.
"""

from __future__ import print_function
import re
import socket
import requests
import xml.etree.ElementTree as ET
import numpy

def is_ncar_host():
    """Determine if host is an NCAR machine."""
    hostname = socket.getfqdn()
    
    return any([re.compile(ncar_host).search(hostname) 
                for ncar_host in ['cheyenne', 'casper', 'hobart']])


# Author: Unknown
# I got the original version from a word document published by ESGF
# https://docs.google.com/document/d/1pxz1Kd3JHfFp8vR2JCVBfApbsHmbUQQstifhGNdc6U0/edit?usp=sharing

# API AT: https://github.com/ESGF/esgf.github.io/wiki/ESGF_Search_REST_API#results-pagination

def esgf_search(server="https://esgf-node.llnl.gov/esg-search/search",
                #server="https://esgf-node.ipsl.upmc.fr/esg-search/search",
                #server="https://esgf-data.dkrz.de/esg-search/search",
                files_type="OPENDAP", local_node=True, project="CMIP6",
                verbose=False, format="application%2Fsolr%2Bjson",
                use_csrf=False, **search):
    client = requests.session()
    payload = search
    payload["project"] = project
    payload["type"]= "File"
    if local_node:
        payload["distrib"] = "false"
    if use_csrf:
        client.get(server)
        if 'csrftoken' in client.cookies:
            # Django 1.6 and up
            csrftoken = client.cookies['csrftoken']
        else:
            # older versions
            csrftoken = client.cookies['csrf']
        payload["csrfmiddlewaretoken"] = csrftoken

    payload["format"] = format

    offset = 0
    numFound = 10000
    all_files = []
    files_type = files_type.upper()
    while offset < numFound:
        payload["offset"] = offset
        url_keys = [] 
        for k in payload:
            url_keys += ["{}={}".format(k, payload[k])]

        url = "{}/?{}".format(server, "&".join(url_keys))
        print(url)
        r = client.get(url)
        r.raise_for_status()
        resp = r.json()["response"]
        numFound = int(resp["numFound"])
        resp = resp["docs"]
        offset += len(resp)
        for d in resp:
            if verbose:
                for k in d:
                    print("{}: {}".format(k,d[k]))
            url = d["url"]
            for f in d["url"]:
                sp = f.split("|")
                if sp[-1] == files_type:
                    all_files.append(sp[0].split(".html")[0])
    return sorted(all_files)


## Summary of some test data

| model name | resolution | years in file for one variable | file size (one variable) | combined 3D variable data size | combined 2D variable data size |
| --- | --- | --- | --- | --- | --- |
| ACCESS-OM2 | 100 km | 10 | 670 MB | 17 GB | 0.4 GB |
| ACCESS-OM2-025 | 25 km | 1 | 1.1 GB | 271 GB | 7 GB |
| CMCC-CM2-SR5 | 100 km | 61 | 3.6 GB | 15 GB | 0.4 GB |
| CMCC-CM2-HR4 | 25 km | 10 | 9.4 GB | 231 GB | 6 GB |


## Problem in data source 

source_id=['CMCC-CM2-SR5','CMCC-CM2-HR4']

These two data set are not in where ldap tells us where they are!!

----
not working
result = esgf_search(activity_id='OMIP', experiment_id='omip2', grid_label='gn', variable_id=var_i, source_id = 'ACCESS-OM2-025') #'CMCC-CM2-HR4') #SR5 #source_id = 'ACCESS-OM2-025')


## Load data from ESGF

In [4]:

#source_id='CMCC-CM2-SR5'
source_id='CMCC-CM2-HR4'
#source_id='ACCESS-OM2-025'

result = esgf_search(activity_id='OMIP'
                          , experiment_id='omip2'
                          , variable_id='vmo'
                          , source_id=source_id)
                          # works, source_id='ACCESS-OM2-025')
                          # works, source_id='ACCESS-OM2')
#CMCC-CM2-SR5')

https://esgf-node.llnl.gov/esg-search/search/?activity_id=OMIP&experiment_id=omip2&variable_id=vmo&source_id=CMCC-CM2-HR4&project=CMIP6&type=File&distrib=false&format=application%2Fsolr%2Bjson&offset=0


ConnectionError: HTTPSConnectionPool(host='esgf-node.llnl.gov', port=443): Max retries exceeded with url: /esg-search/search/?activity_id=OMIP&experiment_id=omip2&variable_id=vmo&source_id=CMCC-CM2-HR4&project=CMIP6&type=File&distrib=false&format=application%2Fsolr%2Bjson&offset=0 (Caused by NewConnectionError('<urllib3.connection.HTTPSConnection object at 0x7f97472fb250>: Failed to establish a new connection: [Errno 110] Connection timed out'))

In [ ]:
result
files_to_open = [result[-1]]
url=result[-1]
url

In [ ]:
ds =xr.open_mfdataset([url], decode_times=False, engine="pydap")
ds
#test.to_zarr('test.zarr')

In [ ]:
test=ds[['vmo']].isel(time= 0,lev=0 )


In [14]:
test

<xarray.Dataset>
Dimensions:    (time: 132, lev: 50, j: 1050, i: 1440)
Coordinates:
  * time       (time) float64 1.296e+05 1.296e+05 ... 1.335e+05 1.336e+05
  * lev        (lev) float64 0.5126 1.621 2.858 ... 5.1e+03 5.498e+03 5.904e+03
  * j          (j) int32 0 1 2 3 4 5 6 7 ... 1043 1044 1045 1046 1047 1048 1049
  * i          (i) int32 0 1 2 3 4 5 6 7 ... 1433 1434 1435 1436 1437 1438 1439
    latitude   (j, i) float64 dask.array<chunksize=(1050, 1440), meta=np.ndarray>
    longitude  (j, i) float64 dask.array<chunksize=(1050, 1440), meta=np.ndarray>
Data variables:
    vmo        (time, lev, j, i) float32 dask.array<chunksize=(132, 50, 1050, 1440), meta=np.ndarray>
Attributes: (12/39)
    Conventions:                     CF-1.7 CMIP-6.2
    activity_id:                     OMIP
    comment:                         Ocean initial conditions: WOA 2013 T & S...
    contact:                         Pier Giuseppe Fogli (piergiuseppe.fogli@...
    creation_date:                   2020-01-31T21:19:12Z
    data_specs_version:              01.00.31
    ...                              ...
    variable_id:                     vmo
    variant_label:                   r1i1p1f1
    license:                         CMIP6 model data produced by CMCC is lic...
    cmor_version:                    3.5.0
    tracking_id:                     hdl:21.14100/a54c0833-3909-4ed4-b5eb-e57...
    DODS_EXTRA.Unlimited_Dimension:  time

In [ ]:
test.where(ds.latitude>80,drop=True)

/srv/conda/envs/notebook/lib/python3.9/site-packages/xarray/core/indexing.py:1380: PerformanceWarning: Slicing is producing a large chunk. To accept the large
chunk and silence this warning, set the option
    >>> with dask.config.set(**{'array.slicing.split_large_chunks': False}):
    ...     array[indexer]

To avoid creating the large chunks, set the option
    >>> with dask.config.set(**{'array.slicing.split_large_chunks': True}):
    ...     array[indexer]
  value = value[(slice(None),) * axis + (subkey,)]


In [ ]:
test=_

In [73]:
import hvplot
import hvplot.xarray
test.hvplot.quadmesh(y='latitude',x='longitude')

:QuadMesh   [longitude,latitude]   (vmo)

In [74]:
test.to_zarr('CMCC-CM2-SR5.zarr')

## I do not understand.  above ldap didn't work for CMCC-CM2-SR5 a few days ago, and now it is working.....